In [1]:
from __future__ import print_function

import sys
import numpy as np
from sklearn.preprocessing import QuantileTransformer
from sklearn.model_selection import train_test_split

sys.path.append('..')
import tensorflow as tf
#from supplementary_code_direct_ranker.DirectRanker import directRanker
#from supplementary_code_direct_ranker.helpers import readData, nDCGScorer_cls, MAP_cls
import DirectRanker as drr
import helpers as hlps

Instructions for updating:
non-resource variables are not supported in the long term


# Read data

In [11]:
# x_test, y_test, q_test = hlps.readData(data_path="/Users/wery/Desktop/BAJiawenWang/dataset/MQ2007/Fold1/test.txt", 
#                                        binary=True, at=10, number_features=46, bin_cutoff=1.5, cut_zeros=True)
# x_train, y_train, q_train = hlps.readData(data_path="/Users/wery/Desktop/BAJiawenWang/dataset/MQ2007/Fold1/train.txt", 
#                                           binary=True, at=10, number_features=46, bin_cutoff=1.5, cut_zeros=True)

# x_test, y_test, q_test = hlps.readData(data_path="/Users/wery/Desktop/BAJiawenWang/dataset/MQ2008/Fold1/test.txt", 
#                                        binary=True, at=10, number_features=46, bin_cutoff=1.5, cut_zeros=True)
# x_train, y_train, q_train = hlps.readData(data_path="/Users/wery/Desktop/BAJiawenWang/dataset/MQ2008/Fold1/train.txt", 
#                                           binary=True, at=10, number_features=46, bin_cutoff=1.5, cut_zeros=True)

x_test, y_test, q_test = hlps.readData(data_path="/Users/wery/Desktop/BAJiawenWang/dataset/OHSUMED/Feature-min/Fold1/testset.txt", 
                                       binary=True, at=10, number_features=45, bin_cutoff=1.5, cut_zeros=True)
x_train, y_train, q_train = hlps.readData(data_path="/Users/wery/Desktop/BAJiawenWang/dataset/OHSUMED/Feature-min/Fold1/trainingset.txt", 
                                          binary=True, at=10, number_features=45, bin_cutoff=1.5, cut_zeros=True)

# x_test, y_test, q_test = hlps.readData(data_path="/Users/wery/Desktop/BAJiawenWang/dataset/TREC/TD2003/Fold1/testset.txt", 
#                                        binary=False, at=10, number_features=44, bin_cutoff=1.5, cut_zeros=True)
# x_train, y_train, q_train = hlps.readData(data_path="/Users/wery/Desktop/BAJiawenWang/dataset/TREC/TD2003/Fold1/trainingset.txt", 
#                                           binary=False, at=10, number_features=44, bin_cutoff=1.5, cut_zeros=True)

# x_test, y_test, q_test = hlps.readData(data_path="/Users/wery/Desktop/BAJiawenWang/dataset/TREC/TD2004/Fold1/testset.txt", 
#                                        binary=False, at=5, number_features=44, bin_cutoff=1.5, cut_zeros=True)
# x_train, y_train, q_train = hlps.readData(data_path="/Users/wery/Desktop/BAJiawenWang/dataset/TREC/TD2004/Fold1/trainingset.txt", 
#                                           binary=False, at=5, number_features=44, bin_cutoff=1.5, cut_zeros=True)

# x_test, y_test, q_test = hlps.readData(data_path="/Users/wery/Desktop/BAJiawenWang/dataset/MSLR-WEB10K/Fold1/test.txt", 
#                                        binary=True, at=10, number_features=136, bin_cutoff=1.5, cut_zeros=True)
# x_train, y_train, q_train = hlps.readData(data_path="/Users/wery/Desktop/BAJiawenWang/dataset/MSLR-WEB10K/Fold1/train.txt", 
#                                           binary=True, at=10, number_features=136, bin_cutoff=1.5, cut_zeros=True)

#only 2 min readData!!!

[array([[ 0.24657907,  0.2554638 ,  0.29362937, ...,  0.11452836,
         0.08237719,  0.11576971],
       [-1.73311253, -1.73311253, -1.73311253, ...,  0.00719463,
         0.00945782,  0.02221702],
       [ 0.24657907,  0.2554638 ,  0.12497883, ..., -0.06590266,
        -0.07549665, -0.07218871],
       ...,
       [-1.73311253, -1.73311253, -1.73311253, ..., -0.2029909 ,
        -0.19400303, -0.20703298],
       [-1.73311253, -1.73311253, -1.73311253, ..., -0.2029909 ,
        -0.19400303, -0.20703298],
       [-1.73311253, -1.73311253, -1.73311253, ..., -0.2029909 ,
        -0.19400303, -0.20703298]])]
[array([[0],
       [0],
       [0],
       [0],
       [0],
       [0],
       [0],
       [0],
       [0],
       [0],
       [0],
       [0],
       [0],
       [0],
       [0],
       [0],
       [0],
       [0],
       [0],
       [0],
       [0],
       [0],
       [0],
       [0],
       [0],
       [0],
       [0],
       [0],
       [0],
       [0],
       [1],
       [0],


In [3]:
#len(x_train) #60??? Why not 63 OHSUMED???
len(q_train)
#len(x_test) #20??? Why not 22 OHSUMED???
# x_train

9219

In [9]:
print(q_train) # [ 1  1  1 ... 63 63 63]

[ 1  1  1 ... 63 63 63]


# Define Ranker

In [5]:
def lambda_cost(nn, y0):
    return tf.reduce_mean(tf.log(1+tf.exp(nn))-nn)


# Load directRanker, train, and test
dr = drr.directRanker(
    feature_activation=tf.nn.tanh,
    ranking_activation=tf.nn.tanh,
    # max_steps=10000,
    # For debugging
    #cost=lambda_cost,
    max_steps=10000,
    print_step=500,
    start_batch_size=3,
    end_batch_size=5,
    start_qids=20,
    end_qids=100,
    feature_bias=True,
    hidden_layers=[100, 50, 5]
)

# Fit

In [6]:
dr.fit(x_train, y_train, ranking=True)

2023-02-13 21:22:00.926083: I tensorflow/compiler/mlir/mlir_graph_optimization_pass.cc:357] MLIR V1 optimization pass is not enabled
2023-02-13 21:22:00.932149: W tensorflow/tsl/platform/profile_utils/cpu_utils.cc:128] Failed to get CPU frequency: 0 Hz


step: 0, value: 1.9865144491195679, samples: 3, queries: 20
step: 500, value: 0.45138946175575256, samples: 3, queries: 21
step: 1000, value: 0.5877430438995361, samples: 3, queries: 23
step: 1500, value: 0.618101954460144, samples: 3, queries: 25
step: 2000, value: 0.371041864156723, samples: 3, queries: 27
step: 2500, value: 0.46808892488479614, samples: 3, queries: 29
step: 3000, value: 0.44313883781433105, samples: 3, queries: 32
step: 3500, value: 0.47596773505210876, samples: 3, queries: 35
step: 4000, value: 0.4019414782524109, samples: 3, queries: 38
step: 4500, value: 0.422284871339798, samples: 3, queries: 41
step: 5000, value: 0.1874166578054428, samples: 3, queries: 44
step: 5500, value: 0.20811422169208527, samples: 3, queries: 48
step: 6000, value: 0.21188651025295258, samples: 4, queries: 52
step: 6500, value: 0.12749722599983215, samples: 4, queries: 56
step: 7000, value: 0.14550602436065674, samples: 4, queries: 61
step: 7500, value: 0.16455361247062683, samples: 4, qu

# Evaluate

In [7]:
hlps.nDCGScorer_cls(dr, x_test, y_test, at=5)
hlps.MAP_cls(dr, x_test, y_test)

nDCG@5: 0.1687 +- 0.1852
MAP: 0.1954 +- 0.1298


0.19543966348002678

In [8]:
# OHSUMED:
# nDCG@5: 0.1035 +- 0.1561
# MAP: 0.1436 +- 0.0978

# MQ2008
# nDCG@5: 0.4944 +- 0.3143
# MAP: 0.4663 +- 0.2943
# nDCG@10: 0.5661 +- 0.279
# MAP: 0.4663 +- 0.2943

# MSLR-WEB10K
# nDCG@10: 0.4109 +- 0.2404
# MAP: 0.3452 +- 0.178